In [1]:
import gymnasium
import push_box
import pybullet as p
import pybullet_data
import time
from stable_baselines3 import PPO
from stable_baselines3.common.vec_env import DummyVecEnv
from stable_baselines3.common.evaluation import evaluate_policy
from stable_baselines3.common.callbacks import EvalCallback, StopTrainingOnRewardThreshold
import os
from typing import Any, Dict
import torch as th

pybullet build time: Nov 28 2023 23:48:36
2024-03-14 13:22:07.599194: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:9261] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-03-14 13:22:07.599218: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:607] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-03-14 13:22:07.600219: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1515] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-03-14 13:22:07.605653: I tensorflow/core/platform/cpu_feature_guard.cc:182] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
202

In [21]:
p.disconnect()

numActiveThreads = 0
stopping threads
Thread with taskId 0 exiting
destroy semaphore
semaphore destroyed
Thread TERMINATED
destroy main semaphore
main semaphore destroyed
finished
numActiveThreads = 0
btShutDownExampleBrowser stopping threads
Thread with taskId 0 exiting
Thread TERMINATED
destroy semaphore
semaphore destroyed
destroy main semaphore
main semaphore destroyed


In [3]:
log_path = os.path.join('Training', 'Logs')

In [10]:
env = gymnasium.make('pushBox-v0')
env = DummyVecEnv([lambda: env])

startThreads creating 1 threads.
starting thread 0
started thread 0 
argc=2
argv[0] = --unused
argv[1] = --start_demo_name=Physics Server
ExampleBrowserThreadFunc started
X11 functions dynamically loaded using dlopen/dlsym OK!
X11 functions dynamically loaded using dlopen/dlsym OK!
Creating context
Created GL 3.3 context
Direct GLX rendering context obtained
Making context current
GL_VENDOR=NVIDIA Corporation
GL_RENDERER=NVIDIA GeForce GTX 1080/PCIe/SSE2
GL_VERSION=3.3.0 NVIDIA 545.23.08
GL_SHADING_LANGUAGE_VERSION=3.30 NVIDIA via Cg compiler
pthread_getconcurrency()=0
Version = 3.3.0 NVIDIA 545.23.08
Vendor = NVIDIA Corporation
Renderer = NVIDIA GeForce GTX 1080/PCIe/SSE2
b3Printf: Selected demo: Physics Server
startThreads creating 1 threads.
starting thread 0
started thread 0 
MotionThreadFunc thread started
ven = NVIDIA Corporation
ven = NVIDIA Corporation


In [11]:
# Add a callback to training stage for early stopping
save_path = os.path.join('Training', 'SavedModels', 'PPO_88_best')
stop_callback = StopTrainingOnRewardThreshold(reward_threshold = 100, verbose = 1)
eval_callback = EvalCallback(env, 
                            callback_on_new_best = stop_callback,
                            eval_freq = 10000, 
                            best_model_save_path = save_path, 
                            verbose = 1)


In [12]:
# Learning rate schedule: linearly decreasing from 0.0007 to 0.0001
def linear_lr(progress_remaining: float):
    start_lr = 0.00006
    end_lr = 0.0003
    return end_lr + (start_lr - end_lr) * progress_remaining

In [13]:
model = PPO('MlpPolicy', env, learning_rate=linear_lr, verbose=1, tensorboard_log=log_path, device='cuda')

Using cuda device


In [7]:
model.learn(total_timesteps=10000000, callback=eval_callback)

Logging to Training/Logs/PPO_88
-----------------------------
| time/              |      |
|    fps             | 763  |
|    iterations      | 1    |
|    time_elapsed    | 2    |
|    total_timesteps | 2048 |
-----------------------------
------------------------------------------
| time/                   |              |
|    fps                  | 512          |
|    iterations           | 2            |
|    time_elapsed         | 7            |
|    total_timesteps      | 4096         |
| train/                  |              |
|    approx_kl            | 0.0035593738 |
|    clip_fraction        | 0.0139       |
|    clip_range           | 0.2          |
|    entropy_loss         | -2.84        |
|    explained_variance   | 0.839        |
|    learning_rate        | 5e-05        |
|    loss                 | -0.0086      |
|    n_updates            | 10           |
|    policy_gradient_loss | -0.00377     |
|    std                  | 0.998        |
|    value_loss           |

/home/danielmasamba/anaconda3/envs/dan/lib/python3.11/site-packages/stable_baselines3/common/evaluation.py:67: UserWarning: Evaluation environment is not wrapped with a ``Monitor`` wrapper. This may result in reporting modified episode lengths and rewards, if other wrappers happen to modify these. Consider wrapping environment first with ``Monitor`` wrapper.
  warnings.warn(


Eval num_timesteps=10000, episode_reward=-1.00 +/- 0.00
Episode length: 500.00 +/- 0.00
------------------------------------------
| eval/                   |              |
|    mean_ep_length       | 500          |
|    mean_reward          | -1           |
| time/                   |              |
|    total_timesteps      | 10000        |
| train/                  |              |
|    approx_kl            | 0.0007733422 |
|    clip_fraction        | 0            |
|    clip_range           | 0.2          |
|    entropy_loss         | -2.83        |
|    explained_variance   | 0.905        |
|    learning_rate        | 5e-05        |
|    loss                 | -0.00122     |
|    n_updates            | 40           |
|    policy_gradient_loss | -0.000646    |
|    std                  | 0.997        |
|    value_loss           | 0.000184     |
------------------------------------------
New best mean reward!
------------------------------
| time/              |       |
|    fps   

In [14]:
PPO_Path = os.path.join('Training', 'SavedModels', 'PPO_88_best/best_model')

In [14]:
# model.save(PPO_Path)

In [15]:
del model

In [16]:
model = PPO.load(PPO_Path, env=env)

In [20]:
evaluate_policy(model, env, n_eval_episodes=10)

box reached target
box reached target
box reached target
box reached target
box reached target
box reached target


(3.115843544451491, 2.981593814561435)

In [17]:
p.disconnect()

numActiveThreads = 0
stopping threads
Thread with taskId 0 exiting
Thread TERMINATED
destroy semaphore
semaphore destroyed
destroy main semaphore
main semaphore destroyed
finished
numActiveThreads = 0
btShutDownExampleBrowser stopping threads
Thread with taskId 0 exiting
Thread TERMINATED
destroy semaphore
semaphore destroyed
destroy main semaphore
main semaphore destroyed
